In [1]:
from google.colab import drive
import os
if not os.path.exists('/gd'):
    drive.mount('/gd')

Mounted at /gd


In [2]:
import torch
from transformers import AutoTokenizer, AutoModelForTokenClassification
from transformers.pipelines.token_classification import TokenClassificationPipeline

In [3]:
model_checkpoint = "Davlan/bert-base-multilingual-cased-ner-hrl"

tokenizer = AutoTokenizer.from_pretrained(model_checkpoint)
model = AutoModelForTokenClassification.from_pretrained(model_checkpoint)

/usr/local/lib/python3.10/dist-packages/huggingface_hub/utils/_token.py:88: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


tokenizer_config.json:   0%|          | 0.00/264 [00:00<?, ?B/s]

config.json:   0%|          | 0.00/1.10k [00:00<?, ?B/s]

vocab.txt:   0%|          | 0.00/996k [00:00<?, ?B/s]

special_tokens_map.json:   0%|          | 0.00/112 [00:00<?, ?B/s]

pytorch_model.bin:   0%|          | 0.00/709M [00:00<?, ?B/s]

In [23]:
model.to("cuda")
pipe = TokenClassificationPipeline(model=model, tokenizer=tokenizer, device='cuda', aggregation_strategy="simple", stride=10)

In [5]:
import numpy as np
import os

# DATA_PATH_FOLDER = "../data/"
DATA_PATH_FOLDER = "/gd/MyDrive/data/"

data = np.load(os.path.join(DATA_PATH_FOLDER, "representation.eng.train.npy"))

In [6]:
data.shape

(1017965, 768)

In [7]:
import pandas as pd

def parse_text(text):
    rows = text.split('\n')
    data = []
    for row in rows:
        tokens = row.strip().split('\n')
        for token in tokens:
            token_info = token.split()
            data.append(token_info)
    return data

In [8]:
with open(os.path.join(DATA_PATH_FOLDER, "eng.testa"), 'r') as file:
    text = file.read()

parsed_data = parse_text(text)
print(max(parsed_data, key=len))
filtered_list = list(filter(lambda x: len(x) == 4, parsed_data))

df = pd.DataFrame(filtered_list, columns=['token', 'tag1', 'tag2', 'tag3'])

df.head()

['-DOCSTART-', '-X-', 'O', 'OCRICKET', 'NNP', 'I-NP', 'O']


token tag1  tag2   tag3
0         CRICKET  NNP  I-NP      O
1               -    :     O      O
2  LEICESTERSHIRE  NNP  I-NP  I-ORG
3            TAKE  NNP  I-NP      O
4            OVER   IN  I-PP      O

In [9]:
text_split_special_token = text.split('-DOCSTART- -X- O O')

In [10]:
doc_split = [doc.split("\n") for doc in text_split_special_token]

In [11]:
doc_token_level_split = [[row.split() for row in doc] for doc in doc_split]

In [12]:
sentence_doc_level = [""]*len(doc_token_level_split)

i = 0
for doc in doc_token_level_split:
    sentence = ""
    for row in doc:
        if(row):
            sentence_doc_level[i] += row[0]
            sentence_doc_level[i] += " "
    # print(sentence)
    i += 1

In [24]:
ner_tags = pipe(sentence_doc_level)

In [28]:
import json
file_path = "/gd/MyDrive/ner_tags_results_bert.json"

for list_of_tags in ner_tags:
    for tag in list_of_tags:
      tag["score"] = tag["score"].astype(np.float64)

with open(file_path, 'w') as file:
    json.dump(ner_tags, file)

In [26]:
ner_tags

[[{'entity_group': 'LOC',
   'score': 0.9612622,
   'word': 'LONDON',
   'start': 66,
   'end': 72},
  {'entity_group': 'PER',
   'score': 0.9997841,
   'word': 'Phil Simmons',
   'start': 108,
   'end': 120},
  {'entity_group': 'ORG',
   'score': 0.99958044,
   'word': 'Leicestershire',
   'start': 151,
   'end': 165},
  {'entity_group': 'ORG',
   'score': 0.9991973,
   'word': 'Somerset',
   'start': 171,
   'end': 179},
  {'entity_group': 'ORG',
   'score': 0.999218,
   'word': 'Essex',
   'start': 336,
   'end': 341},
  {'entity_group': 'ORG',
   'score': 0.999332,
   'word': 'Derbyshire',
   'start': 344,
   'end': 354},
  {'entity_group': 'ORG',
   'score': 0.9993699,
   'word': 'Surrey',
   'start': 359,
   'end': 365},
  {'entity_group': 'ORG',
   'score': 0.99911433,
   'word': 'Kent',
   'start': 397,
   'end': 401},
  {'entity_group': 'ORG',
   'score': 0.9995353,
   'word': 'Nottinghamshire',
   'start': 461,
   'end': 476},
  {'entity_group': 'ORG',
   'score': 0.9988298,
